In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

from time import time
from tqdm import tqdm

import warnings
warnings.simplefilter('ignore')

In [14]:
import geopandas as gpd
import folium, matplotlib, mapclassify
import pyproj
from pyproj import Proj, transform

import reverse_geocoder as rg

from shapely.geometry import Point

In [4]:
path_data = "../../data/"

In [5]:
df_tmja = pd.read_csv(path_data + "E-tmja-2019.csv", sep=';')

In [59]:
type(df_tmja)

pandas.core.frame.DataFrame

In [6]:
df_tmja.head()

dateReferentiel        route longueur  prD  depPrD concessionPrD  absD  \
0      01/01/2019      31D0044       44    0      31             N     0   
1      01/01/2019     31D0044E      762    0      31             N     0   
2      01/01/2019      69D0301     6055    2      69             N  -981   
3      01/01/2019      69D0383    13752    4      69             N  -494   
4      01/01/2019  69D0383BPNL     2408    0      69             N     0   

  cumulD         xD          yD  ...  absF  cumulF         xF          yF zF  \
0      0  511656,78  6204078,36  ...    44      44  511698,51  6204063,93  0   
1      0  511367,22  6204210,06  ...   762     762  511880,76   6203732,4  0   
2      0  844036,84  6510806,45  ...    71    6055  849346,89  6509342,34  0   
3      0   846831,3  6522372,16  ...   544   13752  843537,87   6512429,8  0   
4      0  844982,46  6522772,27  ...   413    2408   846831,3  6522372,16  0   

  anneeMesureTrafic typeComptageTrafic typeComptageTrafic_lib  TMJA  ratio_PL  
0               NaN                NaN                    NaN   NaN       NaN  
1               NaN                NaN                    NaN   NaN       NaN  
2               NaN                NaN                    NaN   NaN       NaN  
3               NaN                NaN                    NaN   NaN       NaN  
4               NaN                NaN                    NaN   NaN       NaN  

[5 rows x 24 columns]

In [7]:
df_tmja['ratio_PL'] = df_tmja['ratio_PL'].str.replace(',', '.')
df_tmja['ratio_PL'] = df_tmja['ratio_PL'].astype(float)
df_tmja['ratio_PL_recomputed'] = df_tmja['ratio_PL'].apply(lambda x: x if x<=40 else x/10)

In [8]:
shp_tmja = gpd.read_file(path_data + "E-tmja2019-shp")
shp_tmja['ratio_PL_recomputed'] = shp_tmja['ratio_PL'].apply(lambda x: x if x<=40 else x/10)
shp_tmja = shp_tmja.set_crs('epsg:2154', allow_override=True)

In [9]:
shp_tmja = add_lat_lon_columns(shp_tmja)
coordinates = [(i[1], i[0]) for i in shp_tmja[['lonD', 'latD']].values]
results = rg.search(coordinates)
shp_tmja['region'] = [i['admin1'] for i in results]
shp_tmja['departement'] = [i['admin2'].replace('Departement de ', '').replace('Departement du ', '').replace('Departement des ', '').replace("Departement d'", '').replace('la ', '').replace("l'", "") for i in results]

Loading formatted geocoded file...


In [10]:
shp_tmja.head()

dateRefere        route  longueur prD depPrD concession   absD  cumulD  \
0  2019-01-01      31D0044      44.0   0     31          N    0.0     0.0   
1  2019-01-01     31D0044E     762.0   0     31          N    0.0     0.0   
2  2019-01-01      69D0301    6055.0   2     69          N -981.0     0.0   
3  2019-01-01      69D0383   13752.0   4     69          N -494.0     0.0   
4  2019-01-01  69D0383BPNL    2408.0   0     69          N    0.0     0.0   

          xD          yD  ...  TMJA ratio_PL  \
0  511656.78  6204078.36  ...     0      0.0   
1  511367.22  6204210.06  ...     0      0.0   
2  844036.84  6510806.45  ...     0      0.0   
3  846831.30  6522372.16  ...     0      0.0   
4  844982.46  6522772.27  ...     0      0.0   

                                            geometry ratio_PL_recomputed  \
0  LINESTRING (511656.785 6204078.361, 511672.731...                 0.0   
1  MULTILINESTRING ((511367.215 6204210.064, 5113...                 0.0   
2  LINESTRING (844036.841 6510806.450, 844044.447...                 0.0   
3  LINESTRING (846831.303 6522372.160, 846865.124...                 0.0   
4  LINESTRING (844982.456 6522772.273, 844995.417...                 0.0   

       lonD       latD      lonF       latF       region          departement  
0  0.695459  42.911382  0.695975  42.911263    Catalonia  Provincia de Lleida  
1  0.691871  42.912490  0.698322  42.908331    Catalonia  Provincia de Lleida  
2  4.850575  45.681629  4.918315  45.667307  Rhone-Alpes                Rhone  
3  4.890020  45.785151  4.844653  45.696348  Rhone-Alpes                Rhone  
4  4.866352  45.789149  4.890020  45.785151  Rhone-Alpes                Rhone  

[5 rows x 32 columns]

In [11]:
print(f'we need one point each {round(shp_tmja.geometry.length.sum())/10000} m')

we need one point each 1882.5978 m


In [12]:
(shp_tmja.geometry.length.sum()/1000)/10000

1.882597830675175

In [45]:
n_coordinates = 10000
total_distance = shp_tmja.geometry.length.sum() # in meters
distance_between_coordinates = total_distance/n_coordinates
points = []
routes = []

for idx in tqdm(shp_tmja.index):
    line = shp_tmja.geometry[idx]
    # print(line)
    route = shp_tmja.route[idx]
    # print(route)
    n_splits = int(line.length/distance_between_coordinates)
    # print(n_splits)
    if n_splits < 2:
        splitter = [line.interpolate((i/2), normalized=True) for i in range(2)]
    else:
        splitter = [line.interpolate((i/n_splits), normalized=True) for i in range(n_splits)]
    
    points.append(splitter)
    routes.append([route for i in (range(n_splits) if n_splits >= 2 else range(2))])
    # print('')
routes = np.concatenate(routes)
# print(len(routes))

100%|████████████████████████████████████| 4695/4695 [00:00<00:00, 11679.92it/s]


In [46]:
coordinates = pd.DataFrame([i.wkt.replace('POINT (', '').replace(')', '').split(' ') for i in np.concatenate(points)])
coordinates.columns = ["easting", "northing"]
coordinates['route'] = routes
coordinates['geometry'] = gpd.points_from_xy(x=coordinates.easting, 
                                             y=coordinates.northing,
                                             crs=shp_tmja.crs)

In [47]:
shp_coordinates = gpd.GeoDataFrame(coordinates)

In [48]:
shp_coordinates

easting           northing     route  \
0        511656.784599997       6204078.3607   31D0044   
1       511677.2349017429  6204069.939337369   31D0044   
2        511367.215000004        6204210.064  31D0044E   
3       511736.9510113234  6204015.573582755  31D0044E   
4        844036.840899996       6510806.4495   69D0301   
...                   ...                ...       ...   
13973  440432.83714999165  6360261.379555852     P0524   
13974          458798.853        6325912.317     P0524   
13975   458011.7067121267  6324604.018405371     P0524   
13976    548722.843000002        6283728.592     P0542   
13977   549187.0439033181  6284311.936804608     P0542   

                             geometry  
0      POINT (511656.785 6204078.361)  
1      POINT (511677.235 6204069.939)  
2      POINT (511367.215 6204210.064)  
3      POINT (511736.951 6204015.574)  
4      POINT (844036.841 6510806.450)  
...                               ...  
13973  POINT (440432.837 6360261.380)  
13974  POINT (458798.853 6325912.317)  
13975  POINT (458011.707 6324604.018)  
13976  POINT (548722.843 6283728.592)  
13977  POINT (549187.044 6284311.937)  

[13978 rows x 4 columns]

In [49]:
# shp_coordinates.to_file(path_data + 'new_coordinates')

In [50]:
shp_coordinates.explore() # [shp_coordinates['route']=='31D0044E'].explore()